In [5]:
import tweepy
import webbrowser
import time
import csv
import os
import tweepy as tw
import pandas as pd
import requests
import json
import searchtweets
from jsonmerge import Merger
import expansions # expansions.py

ModuleNotFoundError: No module named 'tweepy'

In [2]:
# ----------------- attention ------------------------- #
# 
# 1. geo info reduced a lot: https://twittercommunity.com/t/has-geo-search-parameter-outlier-rate-difference-between-v1-1-and-v2-endpoint/152676
#    progress: set geo and go for overall look - most of keywords search don't provide geo info
# 2. rate limit : every 15 mins, each topic only lists 10K tweets




In [52]:
bearer_token='AAAAAAAAAAAAAAAAAAAAAGx0PQEAAAAAU5tboUI%2FMJeuC54BBmLbFLOJybM%3D8IsaqdJKIhqF9wjyrOkDj89M8Iz1U1Rl7rryitHWZREiYRHIpm'

search_url = "https://api.twitter.com/2/tweets/search/all"

In [5]:
# topic1: 5G query_params = {'query':'climatechange has:geo lang:en -is:retweet -is:reply',
query_params = {'query':'5G has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}

In [6]:
FILE = '5G_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "992609029326176257",
            "created_at": "2021-04-29T23:39:55.000Z",
            "geo": {
                "place_id": "0fc3474d6915b000"
            },
            "id": "1387914576784592896",
            "lang": "en",
            "public_metrics": {
                "like_count": 11,
                "quote_count": 0,
                "reply_count": 2,
                "retweet_count": 0
            },
            "text": "Customers are loving this 5G for All Trade in Promo! We\u2019re seeing some vintage devices here at Beach &amp; Talbert \ud83d\ude31 @JonFreier @SamSindha @rwashley1 @JordanaThorburn @AllieAndersenHB https://t.co/2bN2RgL9zR"
        },
        {
            "author_id": "66944716",
            "created_at": "2021-04-29T23:33:03.000Z",
            "geo": {
                "place_id": "3b77caf94bfc81fe"
            },
            "id": "1387912847909220352",
            "lang": "en",
            "public_metrics

200
b26v89c19zqg8o3fostswgr6btbakwti4gs7rnkn84upp
200
b26v89c19zqg8o3fostsh4q5mzi803nacj0xnxs3624jh
200
b26v89c19zqg8o3fostrmvosiokyhhb3danwar8mf68al
200
b26v89c19zqg8o3fostqsiba2xw8j4w5en0936p2niu0t
200
b26v89c19zqg8o3fosqudx95hclh4frtz0mckzblhrl31
200
b26v89c19zqg8o3fosqtj74sfv56df7rt2590xrny8nel
200
b26v89c19zqg8o3fosqrv3vjz47jyha7dtxngdvlet5z1
200
b26v89c19zqg8o3fosnv190f9kqngxlasaazkdywupx8d
200
b26v89c19zqg8o3fosntrny1r42rqwf5991ljoj3cq2rh
200
b26v89c19zqg8o3fosnswzwwnqef8m6f1sug8xu81my65
200
b26v89c19zqg8o3fosnr8hrhbcjbs6jgrbn1y85jl25j1
200
b26v89c19zqg8o3foskuer4b2w76dpgn5sl7xnh4el3lp
200
b26v89c19zqg8o3foskt5iracknh2rrc2wig4cdn8537h
200
b26v89c19zqg8o3foskt53wlpobkzf8j7g5aoieg6ksxp


ChunkedEncodingError: ("Connection broken: ConnectionResetError(54, 'Connection reset by peer')", ConnectionResetError(54, 'Connection reset by peer'))

In [7]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("5G_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df1 = pd.json_normalize(dataset['data'])

In [8]:
df1.head(3)

created_at lang  \
0  2021-04-29T23:39:55.000Z   en   
1  2021-04-29T23:33:03.000Z   en   
2  2021-04-29T23:02:52.000Z   en   

                                                text                   id  \
0  Customers are loving this 5G for All Trade in ...  1387914576784592896   
1  These 5G speeds are crazy! @TMobile #WeWontSto...  1387912847909220352   
2  This reads very strangely because it’s an inco...  1387905252066832384   

            author_id      geo.place_id     geo.name geo.country_code  \
0  992609029326176257  0fc3474d6915b000     T-Mobile               US   
1            66944716  3b77caf94bfc81fe  Los Angeles               US   
2            18609072  91eb113282d003a1      Lansing               US   

  geo.country            geo.id  ... author.username  \
0  Etats-Unis  0fc3474d6915b000  ...   elMartinMoore   
1  Etats-Unis  3b77caf94bfc81fe  ...      BPalomoTMO   
2  Etats-Unis  91eb113282d003a1  ...         JPughMI   

  author.public_metrics.followers_count author.public_metrics.following_count  \
0                                   360                                   477   
1                                   137                                   959   
2                                  5377                                  2684   

  author.public_metrics.tweet_count  author.public_metrics.listed_count  \
0                               621                                   0   
1                               125                                   2   
2                             15426                                 143   

            author.id   author.name  \
0  992609029326176257  Martin Moore   
1            66944716  Berny Palomo   
2            18609072   Joshua Pugh   

                             author.location geo.coordinates.type  \
0                                        NaN                  NaN   
1                            Los Angeles, CA                  NaN   
2  No more than 6 miles from a body of water                  NaN   

  geo.coordinates.coordinates  
0                         NaN  
1                         NaN  
2                         NaN  

[3 rows x 29 columns]

In [9]:
df1['geo.country_code']

0       US
1       US
2       US
3       NZ
4       US
        ..
7264    US
7265    US
7266    US
7267    US
7268    US
Name: geo.country_code, Length: 7269, dtype: object

In [10]:
# topic2: pizza
query_params = {'query':'pizza has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'pizza_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "14536817",
            "created_at": "2021-04-29T23:57:36.000Z",
            "geo": {
                "coordinates": {
                    "coordinates": [
                        -96.007694,
                        41.283015
                    ],
                    "type": "Point"
                },
                "place_id": "a84b808ce3f11719"
            },
            "id": "1387919025590525953",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "Draft day pizza and wings @ Benson https://t.co/9xEsAUy3UH"
        },
        {
            "author_id": "2627988949",
            "created_at": "2021-04-29T23:56:11.000Z",
            "geo": {
                "place_id": "d07feb9e5b1ce37c"
            },
            "id": "1387918667506065413",
         

200
b26v89c19zqg8o3fosttqawn9v7v3ryg9tqvyu0ne07st
200
b26v89c19zqg8o3fosttbfyxputqlyklclum5295c8zul
200
b26v89c19zqg8o3fosttb5ci9fyqpxvv63e28bd8vqph9
200
b26v89c19zqg8o3fostswencjrwhi0fd9bh3w0j9c9enx
200
b26v89c19zqg8o3fostswabsolb4f0tssx1uwsaqaorr1
200
b26v89c19zqg8o3fostsvxljg5w0htnekzwlhbw7pa64d
200
b26v89c19zqg8o3fostsh4ryf2l4sl1dqxjhj4kzu55kt
200
b26v89c19zqg8o3fostsgw8qqq2xnw60xm35l32ossl8d
200
b26v89c19zqg8o3fosts23evavv1xixqzhb8oye64g3ul
200
b26v89c19zqg8o3fosts1ux5tqold82luwu1wb7pw18ql
200
b26v89c19zqg8o3fosts1oi31zpx9vapn8rdpvl75bypp
200
b26v89c19zqg8o3fostrmvpeb4vkuhdiwvudy8pmm80vx
200
b26v89c19zqg8o3fostrmp8ijq57m6hyop7lkcmzex5kt
200
b26v89c19zqg8o3fostr7ucloqirlwyfxv3fnl9uwmjjx
200
b26v89c19zqg8o3fostr7jooa7un74q54ttxkm40x9ev1
200
b26v89c19zqg8o3fostr7d8e86o19at3vq07gq2ov2ef1
200
b26v89c19zqg8o3fostqsmjj7xdrg2h8sqssi8ghwv5od
200
b26v89c19zqg8o3fostqsg6k6p16wyvaw2v9cnstkkg3h
200
b26v89c19zqg8o3fostqs7p5eymbqr46eyqsk5bhcktx9
200
b26v89c19zqg8o3fosqut510mf101l2ev8n2ewiz5vn25


ChunkedEncodingError: ("Connection broken: ConnectionResetError(54, 'Connection reset by peer')", ConnectionResetError(54, 'Connection reset by peer'))

In [11]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("pizza_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df2 = pd.json_normalize(dataset['data'])

In [12]:
df2.head(2)

text   author_id  \
0  Draft day pizza and wings @ Benson https://t.c...    14536817   
1                                      Pizza or pho🤔  2627988949   

                    id lang                created_at      geo.place_id  \
0  1387919025590525953   en  2021-04-29T23:57:36.000Z  a84b808ce3f11719   
1  1387918667506065413   en  2021-04-29T23:56:11.000Z  d07feb9e5b1ce37c   

  geo.coordinates.type geo.coordinates.coordinates geo.place_type  \
0                Point     [-96.007694, 41.283015]           city   
1                  NaN                         NaN           city   

  geo.country_code  ... public_metrics.quote_count author.username  \
0               US  ...                          0        maizie45   
1               US  ...                          0     mberumen96_   

            author.name   author.id author.location         author.created_at  \
0  Maggie ScobeyAustgen    14536817        Nebraska  2008-04-25T23:48:40.000Z   
1     Magdaleno Berumen  2627988949             NaN  2014-07-12T17:46:23.000Z   

   author.public_metrics.followers_count  \
0                                   1634   
1                                     84   

   author.public_metrics.following_count  author.public_metrics.tweet_count  \
0                                   3622                              34555   
1                                     69                               3878   

   author.public_metrics.listed_count  
0                                  38  
1                                   0  

[2 rows x 29 columns]

In [13]:
df2['geo.country_code']

0        US
1        US
2        US
3        US
4        US
         ..
11845    US
11846    US
11847    BR
11848    US
11849    US
Name: geo.country_code, Length: 11850, dtype: object

In [14]:
# topic3 : (covid OR corona)

In [18]:
query_params = {'query':' (covid OR corona) has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'covid_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "2577843229",
            "created_at": "2021-04-29T23:59:42.000Z",
            "geo": {
                "place_id": "70d9237ded8be5f4"
            },
            "id": "1387919552978243589",
            "lang": "pt",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "Covid ou tpm?"
        },
        {
            "author_id": "310069117",
            "created_at": "2021-04-29T23:59:16.000Z",
            "geo": {
                "place_id": "01f0c08d4a4a3983"
            },
            "id": "1387919445612318722",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "A new study by Public Health England (PHE

200
b26v89c19zqg8o3fosttqptqltqbqzwi72gwgz6tres8t
200
b26v89c19zqg8o3fosttqpt4qbrmy47ca0t23ta60ok8t
200
b26v89c19zqg8o3fosttqnqi5ihgk2285vixdp8hog3nh
200
b26v89c19zqg8o3fosttqnplp7jd4x71827xv12zwoakd
200
b26v89c19zqg8o3fosttqnoehzmpsdiuusxc1u2h3xgn1
200
b26v89c19zqg8o3fosttqll6jvmxm8sewg1zlip2dyohp
200
b26v89c19zqg8o3fosttqljz82dfhnoe731glyuynj33x
200
b26v89c19zqg8o3fosttqjgr3y8hrzvb8x4xln4z6coe5
200
b26v89c19zqg8o3fosttqjf95rnkjwf9pq27rqwgq7725
200
b26v89c19zqg8o3fosttqhcbo06vz6nt5fbl8mk43b9ml
200
b26v89c19zqg8o3fosttqhbfgs4ns5dkincv93gxfmb99
200
b26v89c19zqg8o3fosttqhatmtfkt9am2w373hxgm6r25
200
b26v89c19zqg8o3fosttqf8750jbi60djup5zi1c9ha4d
200
b26v89c19zqg8o3fosttqf7an7lvwqimpztg4aiule8ot
200
b26v89c19zqg8o3fosttqf63m0hcg94nyzhch84ttjuyl
200
b26v89c19zqg8o3fosttqd36dcjlrpivj0gduiku0plrx
200
b26v89c19zqg8o3fosttqd1z95vmopc3z8vbq006ozhbx
200
b26v89c19zqg8o3fosttqd0rxebkql9as4kq7cnn0ibgd
200
b26v89c19zqg8o3fosttqaxjrpn1b1lsh4jomwvscf531
200
b26v89c19zqg8o3fosttqawn6u6xicragbpp1juidqirh


ConnectionError: ('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))

In [19]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("covid_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df3 = pd.json_normalize(dataset['data'])

In [20]:
df3['geo.country_code']

0        TH
1        US
2        IN
3        US
4        CA
         ..
14181    IN
14182    NZ
14183    IN
14184    IN
14185    IN
Name: geo.country_code, Length: 14186, dtype: object

In [21]:
# topic 4 : bitcoin

In [34]:
query_params = {'query':'bitcoin has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'bitcoin_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "2670899293",
            "created_at": "2021-04-29T23:57:10.000Z",
            "geo": {
                "place_id": "bceb8153865c4a49"
            },
            "id": "1387918916001882114",
            "lang": "en",
            "public_metrics": {
                "like_count": 2,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "We did it first.. #Bitcoin https://t.co/uaehc1C5tB"
        },
        {
            "author_id": "2424272810",
            "created_at": "2021-04-29T23:51:32.000Z",
            "geo": {
                "place_id": "ecd2c278e0024985"
            },
            "id": "1387917497244946434",
            "lang": "en",
            "public_metrics": {
                "like_count": 4,
                "quote_count": 0,
                "reply_count": 1,
                "retweet_count": 0
            },
            "text": "I\u

200
b26v89c19zqg8o3fosttbi3o192ateobljrqjl31vym4d
200
b26v89c19zqg8o3fosttb5apebmqjyabnsk3dhn7at5z1
200
b26v89c19zqg8o3fostsw89gz8mzrzpialxswsx94gn0d
200
b26v89c19zqg8o3fostsw1vl2keboue0pm7l2d1f789dp
200
b26v89c19zqg8o3fostsh2nj3omeyi33g1p3jzrp56gl9
200
b26v89c19zqg8o3fostsgry3bun0njmyj886xbktexg1p
200
b26v89c19zqg8o3fosts1z4t37kkf8djuobjatsxmsfi5
200
b26v89c19zqg8o3fosts1me96vcxiwbbgjxt4v2k7xvul
200
b26v89c19zqg8o3fostrmtknzr9tmck8cb93upy6bbc71
200
b26v89c19zqg8o3fostrml0kga6ye2bsuxtzdj9obzzb1
200
b26v89c19zqg8o3fostr7ubehj8zbk8b4fny0iylzl7jx
200
b26v89c19zqg8o3fostr7jn6gmmtd9gexfvrxpzl8h8xp
200
b26v89c19zqg8o3fostqskh7omkg4h4cr533ryrwospkt
200
b26v89c19zqg8o3fostqs7mr83hhid2y98d20v0scuvel
200
b26v89c19zqg8o3fosquswies0sbb0p9pvuh2dpmoikcd
200
b26v89c19zqg8o3fosqudze6dlqko100nouw8pfqltqpp
200
b26v89c19zqg8o3fosqudiergv2h0ggy6uajkk2l7wltp
200
b26v89c19zqg8o3fosqtypjdp7iomxwm8cjqjnc4c3n99
200
b26v89c19zqg8o3fosqtyh1z0is19o8ibhry3u8v00igt


ChunkedEncodingError: ("Connection broken: ConnectionResetError(54, 'Connection reset by peer')", ConnectionResetError(54, 'Connection reset by peer'))

In [35]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("bitcoin_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df4 = pd.json_normalize(dataset['data'])

In [36]:
df4['geo.country_code']

0        US
1        US
2        US
3        CA
4        NZ
         ..
10746    BR
10747    BD
10748    XK
10749    US
10750    BD
Name: geo.country_code, Length: 10751, dtype: object

In [37]:
# topic 5 : Kobe

In [38]:
query_params = {'query':'Kobe has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'Kobe_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "753821162795175936",
            "created_at": "2021-04-29T23:52:53.000Z",
            "geo": {
                "place_id": "01e45bfe50e6b7e6"
            },
            "id": "1387917839995052036",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "Like kobe"
        },
        {
            "author_id": "407303812",
            "created_at": "2021-04-29T23:24:12.000Z",
            "geo": {
                "place_id": "43d2418301bf1a49"
            },
            "id": "1387910621186990084",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "Ayy I remember I was so hurt when Kob

200
b26v89c19zqg8o3fosts1x1vmwszgwz5mgwaj0m9l9njx
200
b26v89c19zqg8o3fostr7uc0bhqfymravkt62kj3qxchp
200
b26v89c19zqg8o3fosqut510pghcup2i82cshnpozlshp
200
b26v89c19zqg8o3fosqtjqbme8yf9i9vq3a9045dp5ev1
200
b26v89c19zqg8o3fosqsp4g3zi5bl8l7mxyidi8ucvhx9
200
b26v89c19zqg8o3fosqrfybeu4vb0so6gbskl3aszp4sd
200
b26v89c19zqg8o3fosnv0ybwbqkzvc7vngcu59nxkdrb1
200
b26v89c19zqg8o3fosnu6rdrkq3fpej8vsensua9uhi0t
200
b26v89c19zqg8o3fosntcbv7zl90zc6i018zyl8gaci2l
200
b26v89c19zqg8o3fosnsx45r5xtin0ic8swxkno0py1z1
200
b26v89c19zqg8o3fosns2zb5no65d2y4ecy2wx0lnic8t
200
b26v89c19zqg8o3fosnr8o5nvvuzd26uemjybs8bk8inx
200
b26v89c19zqg8o3foskuu0xlq3nsbr3uubwj2gspdr2wt
200
b26v89c19zqg8o3fosktzpq123x7qdk26bzsasj8ejszh
200
b26v89c19zqg8o3foskt5ek8dc5q3gm6or0u6mww456yl
200
b26v89c19zqg8o3foskt584uxoetv758l7wow8dlq7tz1
200
b26v89c19zqg8o3foskt5611122j2c5obhzxovikq08l9
200
b26v89c19zqg8o3foskt55zj7izc1im0dtc4z5p7feqgt
200
b26v89c19zqg8o3foskt55ymyr0q6cifw4rh5k3zb7zi5
200
b26v89c19zqg8o3foskt53wau9ekcvt0ncorbhfw8eph9


ConnectionError: ('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))

In [39]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("Kobe_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df5 = pd.json_normalize(dataset['data'])

In [40]:
df5['geo.country_code']

0        TH
1        US
2        US
3        US
4        US
         ..
26831    US
26832    CA
26833    BR
26834    US
26835    US
Name: geo.country_code, Length: 26836, dtype: object

In [41]:
# topic 6 Joe Biden

In [56]:
query_params = {'query':'Biden has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'Biden_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "271241579",
            "created_at": "2021-04-29T23:58:58.000Z",
            "geo": {
                "place_id": "e4a0d228eb6be76b"
            },
            "id": "1387919370161111040",
            "lang": "en",
            "public_metrics": {
                "like_count": 3,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "Joe Biden once again setting unrealistic expectations for tops across the country. https://t.co/Yk7zMYcQVB"
        },
        {
            "author_id": "25377589",
            "created_at": "2021-04-29T23:58:38.000Z",
            "geo": {
                "place_id": "3b77caf94bfc81fe"
            },
            "id": "1387919286685995019",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retw

200
b26v89c19zqg8o3fosttqnq7kov5rnkywlau69c89u3y5
200
b26v89c19zqg8o3fosttqllh36uru4n1zs289ahtrz7ul
200
b26v89c19zqg8o3fosttqjhnk8jfa38l1ou1j5hj8ovi5
200
b26v89c19zqg8o3fosttqjhcru0pqz5erwtf3thqtjngd
200
b26v89c19zqg8o3fosttqjh22fgi2u2mmfdvy1q17wq65
200
b26v89c19zqg8o3fosttqjg5km407l8lawc360bo87725
200
b26v89c19zqg8o3fosttqhb4sx9ezrmsrmpffpjrkdvul
200
b26v89c19zqg8o3fosttqd1oi8hpptmgrdap0l29qouwt
200
b26v89c19zqg8o3fosttq8tpzmy9drynttknf80a6wbjx
200
b26v89c19zqg8o3fosttbk7sfnsbdxd352tbdj2gnuc8t
200
b26v89c19zqg8o3fosttbfymudrwoweo80iv8vzwd3n25
200
b26v89c19zqg8o3fosttb9krhezqd6uk1fnpc7gxevmv1
200
b26v89c19zqg8o3fosttb37rzkrrxxdjiqvvweqdspgn1
200
b26v89c19zqg8o3fostswgrgzp1435ow5h3dssvmksygt
200
b26v89c19zqg8o3fostswadamprdrs9rydper9uckyut9
200
b26v89c19zqg8o3fostsw400n2b97lf7w3l1encr2a0sd
200
b26v89c19zqg8o3fostsw1u35xag6rauws3ewpjdlwmf1
200
b26v89c19zqg8o3fostshb58g9q4yi30lv44p370yq6pp
200
b26v89c19zqg8o3fostsh4rcl3ohltp6njve7a8ledzst
200
b26v89c19zqg8o3fostsh0hlpmrv55u1v2ts3xxi0hchp


ConnectionError: ('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))

In [57]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("Biden_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df6 = pd.json_normalize(dataset['data'])

In [58]:
df6['geo.country_code']

0        US
1        US
2        US
3        JM
4        US
         ..
15266    DE
15267    US
15268    US
15269    US
15270    US
Name: geo.country_code, Length: 15271, dtype: object

In [59]:
# topic 7: Mars

In [66]:
query_params = {'query':'Mars has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'Mars_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "1309115312072265728",
            "created_at": "2021-04-29T23:36:28.000Z",
            "geo": {
                "place_id": "f95304ef80fecc3f"
            },
            "id": "1387913707183763458",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "\u201cOne of the ways to increase the chances of finding your lost pet is having it microchipped.\u201d - Microchipping Your Dog or Cat - https://t.co/p0W2dRgqRb.. https://t.co/k9BddoxF7l"
        },
        {
            "author_id": "946480184760389632",
            "created_at": "2021-04-29T23:28:34.000Z",
            "geo": {
                "place_id": "512a8a4a4c4b4be0"
            },
            "id": "1387911720568504322",
            "lang": "en",
            "public_metrics": {
                "like

200
b26v89c19zqg8o3fostsw6454gs21uh5j76w57swjvaf1
200
b26v89c19zqg8o3fostsh0isvchgqbtvzjgl96y3sbam5
200
b26v89c19zqg8o3fostsgu2j0w7i4xgrw5v0h2q1tcy9p
200
b26v89c19zqg8o3fosts1uvcvk91fpxlg42ecu54ikdj1
200
b26v89c19zqg8o3fostrmkzd91uxz4zbaa61ddo42rlh9
200
b26v89c19zqg8o3fostqsoprfxg0qplk8fbvj0i1zg1od


ConnectionError: HTTPSConnectionPool(host='api.twitter.com', port=443): Max retries exceeded with url: /2/tweets/search/all?query=Mars+has%3Ageo+lang%3Aen+-is%3Aretweet+-is%3Areply&start_time=2020-01-01T00%3A00%3A00Z&end_time=2021-04-30T00%3A00%3A00Z&max_results=500&expansions=geo.place_id%2Cauthor_id&tweet.fields=text%2Cauthor_id%2Ccreated_at%2Cpublic_metrics%2Cgeo%2Clang&user.fields=id%2Cname%2Cusername%2Ccreated_at%2Clocation%2Cpublic_metrics&place.fields=country_code%2Ccountry%2Cgeo%2Cid%2Cplace_type%2Cname&next_token=b26v89c19zqg8o3fostqsoprfxg0qplk8fbvj0i1zg1od (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x11a6a35b0>: Failed to establish a new connection: [Errno 60] Operation timed out'))

In [67]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("Mars_expended1.json", "w") as f:
    f.write(json.dumps(dataset))

df7 = pd.json_normalize(dataset['data'])

In [68]:
df7['geo.country_code']

0       US
1       US
2       GH
3       US
4       US
        ..
7366    DE
7367    NG
7368    RS
7369    US
7370    US
Name: geo.country_code, Length: 7371, dtype: object

In [73]:
# topic 8: cat

In [74]:
query_params = {'query':'cat has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'cat_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "22241383",
            "created_at": "2021-04-29T23:59:38.000Z",
            "geo": {
                "coordinates": {
                    "coordinates": [
                        -122.41005,
                        37.77547
                    ],
                    "type": "Point"
                },
                "place_id": "5a110d312052166f"
            },
            "id": "1387919535617970176",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 0
            },
            "text": "I'm going live, let's have some fun @ Cat Club SF https://t.co/oiHlq8F2an"
        },
        {
            "author_id": "56285396",
            "created_at": "2021-04-29T23:58:55.000Z",
            "geo": {
                "place_id": "18810aa5b43e76c7"
            },
            "id": "1387919357439844356

200
b26v89c19zqg8o3fosttqf8782f8xk7ju3l2z6mqqa9od
200
b26v89c19zqg8o3fosttq8tfbrvfb3auyx9sxsm5xdv99
200
b26v89c19zqg8o3fosttbi4kg20r9872raa18qtf6ddvh
200
b26v89c19zqg8o3fosttbbqopezsq3ahtuhjkm06lory5
200
b26v89c19zqg8o3fosttb5bwt4v5pfy0uxazklkpkqu0t
200
b26v89c19zqg8o3fostswgqa32mols7azkhrzk6a5mvel
200
b26v89c19zqg8o3fostswace7wsquy7jwtm23nwvjrlod
200
b26v89c19zqg8o3fostsw3yiiuy0jua50yh21uvkilz7h
200
b26v89c19zqg8o3fostsvxkxwtbx9mjt13lt973cc48sd
200
b26v89c19zqg8o3fostsh6xa59au1wn0nhlt02utt2u7x
200
b26v89c19zqg8o3fostsh2lfho6jvlikti2jinh8igrct
200
b26v89c19zqg8o3fostsgu4x05srr8psw29ltmqru4399
200
b26v89c19zqg8o3fosts23ekifuazpc5eqvnf4jeq80vx
200
b26v89c19zqg8o3fosts1x1kuhn8dj0n0u9pjqsd4v2bh
200
b26v89c19zqg8o3fosts1qnp8ewjjtumoehh249wm398d
200
b26v89c19zqg8o3fosts1md22nufwk685lpdjjkum070d
200
b26v89c19zqg8o3fostrmvp3b4lobye64lnntoz7retml
200
b26v89c19zqg8o3fostrmrdjp1y98kl6vu4yatsj60cxp
200
b26v89c19zqg8o3fostrml1gqj2l1oqwd6ifk8f48arnh
200
b26v89c19zqg8o3fostr7uclxuwdemwjqy7267ujf8f3x


ConnectionError: ('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))

In [75]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("cat_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df8 = pd.json_normalize(dataset['data'])

In [76]:
df8['geo.country_code']

0        US
1        US
2        US
3        US
4        US
         ..
49458    US
49459    US
49460    BR
49461    US
49462    US
Name: geo.country_code, Length: 49463, dtype: object

In [77]:
# topic 9: PUBG

In [78]:
query_params = {'query':'PUBG has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'PUBG_1.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "127943720",
            "created_at": "2021-04-29T23:54:35.000Z",
            "geo": {
                "coordinates": {
                    "coordinates": [
                        -79.7164011,
                        43.7742911
                    ],
                    "type": "Point"
                },
                "place_id": "1f4df2b4746ddea7"
            },
            "id": "1387918264911556610",
            "lang": "en",
            "public_metrics": {
                "like_count": 0,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 1
            },
            "text": "PUBG Lite is officially shutting down: As scheduled, the low-end version of the battle royale game PUBG called Lite is officially closing down on Thursday (April 29). Recently, the news of PUBG Lite\u2019s shutdown was confirmed by developers Krafton\u2026 https://t.co/wlXfmWGHjQ #Tech"
        },
     

200
b26v89c19zqg8o3fosntrfe8gdcdxo6kd1ma8vsvzxh19
200
b26v89c19zqg8o3fosktkfu13gjrew0jsohe5s79j5pq5
200
b26v89c19zqg8o3foshun7ukphcm0usiqwghiepr1bjwd
200
b26v89c19zqg8o3foseufzscpd91rihzyx3afb8m7buyl
200
b26v89c19zqg8o3fosbvih4dghy23ygvluhf4uez8slml
200
b26v89c19zqg8o3fosbsk5c625miyd8fo4xwy2vpadawt
200
b26v89c19zqg8o3fos8t7lahqndhe61cqz0azke6rdbwd
200
b26v89c19zqg8o3fos5vjawtv7mq597izvmlmsunjc5fh
200
b26v89c19zqg8o3fos5tumc1ar4z3lp82mhu2qyjyux6l
200
b26v89c19zqg8o3fos5t0ltvtbdtmnc5e2bme6rnl4ccd
200
b26v89c19zqg8o3fos5t0d8l159igzbzddufmqbtuzxj1
200
b26v89c19zqg8o3fos5t090xdyn1rh6yj0d3enwgsub99
200
b26v89c19zqg8o3fos5t0900z6bhgla0u2jx5hpe7b919
200
b26v89c19zqg8o3fos5t08zfkfk17d89iwgw7e51oey65
200
b26v89c19zqg8o3fo7mf6ccp8nrxd9kfyw9953507qc1p
200
b26v89c19zqg8o3fo7mc8nye2iewyyl53raousprzoc59
200
b26v89c19zqg8o3fo7jftlv1lyj130lahxnfzjzfsgxh9
200
b26v89c19zqg8o3fo7jezpkuq7woghfs7qupfs6n88inx
200
b26v89c19zqg8o3fo7jdqd1yx6n2p9p9fw2b1idsubczh
200
b26v89c19zqg8o3fo7jcgnng4rbxhpb2865tt03w3nczh


In [79]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("PUBG_expanded1.json", "w") as f:
    f.write(json.dumps(dataset))

df9 = pd.json_normalize(dataset['data'])

In [80]:
df9['geo.country_code']

0        CA
1        ZW
2        AE
3        IN
4        PK
         ..
17845    IN
17846    US
17847    PH
17848    US
17849    US
Name: geo.country_code, Length: 17850, dtype: object

In [81]:
# topic 10 climatechange

In [82]:
query_params = {'query':'climatechange has:geo lang:en -is:retweet -is:reply',
                'start_time':'2020-01-01T00:00:00Z',
                'end_time':'2021-04-30T00:00:00Z',
                'max_results':'500',
                'expansions': 'geo.place_id,author_id',
                'tweet.fields': 'text,author_id,created_at,public_metrics,geo,lang',
                'user.fields': 'id,name,username,created_at,location,public_metrics',
                'place.fields': 'country_code,country,geo,id,place_type,name',
                'next_token': {}}
FILE = 'climate_2.json'
def create_headers(bearer_token):
    headers = {"Authorization": "Bearer {}".format(bearer_token)}
    return headers

def connect_to_endpoint(url, headers, params):
    response = requests.request("GET", search_url, headers=headers, params=params)
    print(response.status_code)
    if response.status_code != 200:
        raise Exception(response.status_code, response.text)
    return response.json()

def main():
    headers = create_headers(bearer_token)

    json_response = connect_to_endpoint(search_url, headers, query_params)
    print(json.dumps(json_response, indent=4, sort_keys=True))
    #json_response = expansions.flatten(json_response)
    
    with open(FILE, mode='a') as json_file:
        json_file.write(json.dumps(json_response))
        json_file.write("\n")  

    
    while json_response["meta"]["next_token"]:
        time.sleep(2)
        query_params["next_token"] = json_response["meta"]["next_token"]
        json_response = connect_to_endpoint(search_url, headers, query_params)
        #json_response = expansions.flatten(json_response)
        
        with open(FILE, mode='a') as json_file:
            json_file.write(json.dumps(json_response))
            json_file.write("\n")  

        if 'next_token' in json_response["meta"]:
            print(json_response["meta"]["next_token"])
        else:
            break

if __name__ == "__main__":
    main()

200
{
    "data": [
        {
            "author_id": "16967345",
            "created_at": "2021-04-29T22:56:40.000Z",
            "geo": {
                "place_id": "b90f2a335f8565c0"
            },
            "id": "1387903689503887360",
            "lang": "en",
            "public_metrics": {
                "like_count": 3,
                "quote_count": 0,
                "reply_count": 0,
                "retweet_count": 1
            },
            "text": "Innovators come in all shapes, sizes and philosophies. Here\u2019s how a fantastic California company is leading the effort to develop clean renewable fuels to fight #climatechange #caleg https://t.co/9lBqvQmGtm"
        },
        {
            "author_id": "21383841",
            "created_at": "2021-04-29T22:37:30.000Z",
            "geo": {
                "place_id": "3b77caf94bfc81fe"
            },
            "id": "1387898868558225408",
            "lang": "en",
            "public_metrics": {
                "l

200
b26v89c19zqg8o3fosqut527v4x61wf1jkgr5ijo8bekd
200
b26v89c19zqg8o3fosqsp4gekc795jghjmhgiciz87wcd
200
b26v89c19zqg8o3fosqr09hffdg3rztikcm1yz5oei73x
200
b26v89c19zqg8o3fosnsx8genu2yf1bs5ao62fuc1tugt
200
b26v89c19zqg8o3fosnr8wmh5rp5nacdnej19evnj4by5
200
b26v89c19zqg8o3fosktkqiuyc2yme5ghx0srfgnn7drx
200
b26v89c19zqg8o3foskrvzsfs7efmb21peweh13sny8vx
200
b26v89c19zqg8o3foshu7rl06akcwyzajq6fbdjnaowvx
200
b26v89c19zqg8o3foshrotwgc8rr9i3hwhto44q8ug9z1
200
b26v89c19zqg8o3foseufztk158tpqbzuheb7wfreiikd
200
b26v89c19zqg8o3fosesrho53vgvxri34dhaaow3y6vzx
200
b26v89c19zqg8o3fosbvih4z1draxhf00jv3tq135x3el
200
b26v89c19zqg8o3fosbu8w138lqrhmt5v44usgtc89egt
200
b26v89c19zqg8o3fosbszf85xslvq0s52f96nvprx3zp9
200
b26v89c19zqg8o3fos8w5kbjd6dam8ig2lw8tb49yz6nx
200
b26v89c19zqg8o3fos8uh8k06j7fkg3r2oy3okfld3pfh


ConnectionError: HTTPSConnectionPool(host='api.twitter.com', port=443): Max retries exceeded with url: /2/tweets/search/all?query=climatechange+has%3Ageo+lang%3Aen+-is%3Aretweet+-is%3Areply&start_time=2020-01-01T00%3A00%3A00Z&end_time=2021-04-30T00%3A00%3A00Z&max_results=500&expansions=geo.place_id%2Cauthor_id&tweet.fields=text%2Cauthor_id%2Ccreated_at%2Cpublic_metrics%2Cgeo%2Clang&user.fields=id%2Cname%2Cusername%2Ccreated_at%2Clocation%2Cpublic_metrics&place.fields=country_code%2Ccountry%2Cgeo%2Cid%2Cplace_type%2Cname&next_token=b26v89c19zqg8o3fos8uh8k06j7fkg3r2oy3okfld3pfh (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x117846160>: Failed to establish a new connection: [Errno 60] Operation timed out'))

In [83]:
schema = {
  "properties": {
    "data": {
      "mergeStrategy": "append"
    },
    "includes": {
      "type": "object",
      "properties": {
        "users": {
          "mergeStrategy": "append"
        },
        "start_times": {
          "mergeStrategy": "append"
        },
        "end_times": {
          "mergeStrategy": "append"
        },
        "tweets": {
          "mergeStrategy": "append"
        },
        "places": {
          "mergeStrategy": "append"
        },
        "expansions": {
          "mergeStrategy": "append"
        }
      }
    }
  }
}

merger = Merger(schema)

dataset = {}

with open(FILE, "r") as f:
    for line in f.readlines():
        dataset = merger.merge(dataset, json.loads(line))

dataset = expansions.flatten(dataset)

with open("climate_expanded2.json", "w") as f:
    f.write(json.dumps(dataset))

df10= pd.json_normalize(dataset['data'])

In [84]:
df10['geo.country_code']

0       US
1       US
2       AU
3       US
4       US
        ..
8460    US
8461    DE
8462    US
8463    IN
8464    CA
Name: geo.country_code, Length: 8465, dtype: object

In [85]:
# merge files into one file

In [86]:
df1.columns

Index(['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates'],
      dtype='object')

In [87]:
df2= df2[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [88]:
df3= df3[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [89]:
df4= df4[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [90]:
df5= df5[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [91]:
df6= df6[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [92]:
df7= df7[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [93]:
df8= df8[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [94]:
df9= df9[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [95]:
df10= df10[['created_at', 'lang', 'text', 'id', 'author_id', 'geo.place_id',
       'geo.name', 'geo.country_code', 'geo.country', 'geo.id',
       'geo.place_type', 'geo.geo.type', 'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at', 'author.username',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 'author.id', 'author.name',
       'author.location', 'geo.coordinates.type',
       'geo.coordinates.coordinates']]

In [96]:
frames = [df1, df2, df3, df4, df5, df6, df7, df8, df9, df10]
Total_data = pd.concat(frames)

In [97]:
#Total_data.to_csv('Total_data.csv', encoding='utf-8', index=False)

In [107]:
#Total_data.head(3)

In [151]:
mydata= Total_data[['created_at', 'text', 'id', 'author_id', 
       'geo.name', 'geo.country_code',  'geo.country',
       'geo.place_type',  'geo.geo.bbox', 'geo.full_name',
       'public_metrics.retweet_count', 'public_metrics.reply_count',
       'public_metrics.like_count', 'public_metrics.quote_count',
       'author.created_at',
       'author.public_metrics.followers_count',
       'author.public_metrics.following_count',
       'author.public_metrics.tweet_count',
       'author.public_metrics.listed_count', 
       'author.location']]

In [152]:
#mydata.to_csv('mydata.csv', encoding='utf-8', index=False)

In [153]:
mydata.head(2)

created_at  \
0  2021-04-29T23:39:55.000Z   
1  2021-04-29T23:33:03.000Z   

                                                text                   id  \
0  Customers are loving this 5G for All Trade in ...  1387914576784592896   
1  These 5G speeds are crazy! @TMobile #WeWontSto...  1387912847909220352   

            author_id     geo.name geo.country_code geo.country  \
0  992609029326176257     T-Mobile               US  Etats-Unis   
1            66944716  Los Angeles               US  Etats-Unis   

  geo.place_type                                       geo.geo.bbox  \
0            poi  [-117.98766875335787, 33.70094049431383, -117....   
1           city   [-118.668404, 33.704538, -118.155409, 34.337041]   

     geo.full_name  public_metrics.retweet_count  public_metrics.reply_count  \
0         T-Mobile                             0                           2   
1  Los Angeles, CA                             1                           1   

   public_metrics.like_count  public_metrics.quote_count  \
0                         11                           0   
1                         16                           1   

          author.created_at  author.public_metrics.followers_count  \
0  2018-05-05T03:36:49.000Z                                    360   
1  2009-08-19T08:04:12.000Z                                    137   

   author.public_metrics.following_count  author.public_metrics.tweet_count  \
0                                    477                                621   
1                                    959                                125   

   author.public_metrics.listed_count  author.location  
0                                   0              NaN  
1                                   2  Los Angeles, CA